In [13]:
#!pip install pandas
#%matplotlib inline
import math
import numpy as np
import pandas as pd
import pandasql as ps
import scipy.stats as stats
import matplotlib.pyplot as plt
import seaborn as sn
import IPython.display as ipd
import random
import ast
import keras
import tensorflow as tf

from pandas.api.types import CategoricalDtype
from collections import Counter
from collections import defaultdict
from imblearn.over_sampling import RandomOverSampler
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from keras.callbacks import EarlyStopping, ModelCheckpoint
from keras import backend as K
from pandas.api.types import CategoricalDtype
from scikitplot.metrics import plot_cumulative_gain
from scikitplot.metrics import plot_lift_curve
from scikitplot.metrics import plot_precision_recall
from scikitplot.metrics import plot_roc
from sklearn.decomposition import PCA
from sklearn.metrics import accuracy_score, f1_score, classification_report
from sklearn.metrics import roc_curve, auc, roc_auc_score
from sklearn.metrics import roc_curve, auc, roc_auc_score
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.neural_network import MLPClassifier
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import StandardScaler
from sklearn.tree import DecisionTreeClassifier
from sklearn import tree
from tqdm.notebook import tqdm, trange
from collections import defaultdict
from scipy.stats.stats import pearsonr
from keras.models import Sequential
from keras.layers import Dense
from sklearn.preprocessing import MinMaxScaler

plt.rcParams['axes.formatter.useoffset']=False
pd.set_option('display.max_columns', None)
plt.rcParams['figure.figsize'] = [20, 10]
plt.rcParams['figure.dpi'] = 150

def report(results, n_top=3):
    for i in range(1, n_top + 1):
        candidates = np.flatnonzero(results['rank_test_score'] == i)
        for candidate in candidates:
            print("Model with rank: {0}".format(i))
            print("Mean validation score: {0:.3f} (std: {1:.3f})".format(
                  results['mean_test_score'][candidate],
                  results['std_test_score'][candidate]))
            print("Parameters: {0}".format(results['params'][candidate]))
            print("")

In [14]:
df = pd.read_csv('nn.csv', index_col=0)

In [15]:
df.head()

ALBUM_date_released_year  ALBUM_favorites ALBUM_type ALBUM_tags  \
track_id                                                                    
2                           2009.0              4.0      Album         []   
3                           2009.0              4.0      Album         []   
5                           2009.0              4.0      Album         []   
10                          2008.0              4.0      Album         []   
134                         2009.0              4.0      Album         []   

          ALBUM_tracks  ALBUM_listens           ALBUM_title SET_subset  \
track_id                                                                 
2                  7.0         6073.0  AWOL - A Way Of Life      small   
3                  7.0         6073.0  AWOL - A Way Of Life     medium   
5                  7.0         6073.0  AWOL - A Way Of Life      small   
10                 2.0        47632.0     Constant Hitmaker      small   
134                7.0         6073.0  AWOL - A Way Of Life     medium   

          ARTIST_favorites ARTIST_location              ARTIST_tags  \
track_id                                                              
2                 2.302585      New Jersey                 ['awol']   
3                 2.302585      New Jersey                 ['awol']   
5                 2.302585      New Jersey                 ['awol']   
10                4.317488             NaN  ['philly', 'kurt vile']   
134               2.302585      New Jersey                 ['awol']   

         ARTIST_name  TRACK_duration  TRACK_favorites TRACK_genre_top  \
track_id                                                                
2               AWOL             168         1.098612         Hip-Hop   
3               AWOL             237         0.693147         Hip-Hop   
5               AWOL             206         1.945910         Hip-Hop   
10         Kurt Vile             161         5.187386             Pop   
134             AWOL             207         1.386294         Hip-Hop   

         TRACK_genres_all TRACK_genres  TRACK_interest  TRACK_listens  \
track_id                                                                
2                    [21]       ['21']        8.446127       7.165493   
3                    [21]       ['21']        7.293698       6.244167   
5                    [21]       ['21']        7.567346       7.049255   
10                   [10]       ['10']       10.912941      10.822495   
134                  [21]       ['21']        7.027315       6.850126   

         TRACK_tags   TRACK_title  TRACK_number  rmsekurtosis01  rmsemax01  \
track_id                                                                     
2                []          Food             3        2.499856  14.748096   
3                []  Electric Ave             4       -0.643963   9.096919   
5                []    This World             6        0.001781  11.031059   
10               []       Freeway             1        1.766149  12.318485   
134              []  Street Music             5        2.133233  14.236425   

          rmsemean01  rmsemedian01  rmsemin01  rmseskew01  rmsestd01  \
track_id                                                               
2           3.188761      2.653895        0.0    1.565426   2.536809   
3           3.607359      3.706424        0.0    0.018619   1.952665   
5           3.251386      2.409692        0.0    1.026818   2.585286   
10          3.893810      3.756495        0.0    0.825354   2.004721   
134         3.310689      2.912786        0.0    1.230100   2.462405   

          spectral_bandwidthkurtosis01  spectral_bandwidthmax01  \
track_id                                                          
2                             3.874384              3451.105957   
3                             2.383340              3469.176514   
5                             0.895442              3492.736816   
10                            0.437628    

In [16]:
features = [
 'chroma_censkurtosis',
 'chroma_censmax',
 'chroma_censmean',
 'chroma_censmedian',
 'chroma_censmin',
 'chroma_censskew',
 'chroma_censstd',
 'chroma_censcqtkurtosis',
 'chroma_cqtmax',
 'chroma_cqtmean',
 'chroma_cqtmedian',
 'chroma_cqtmin',
 'chroma_cqtskew',
 'chroma_cqtstd',
 'chroma_stftkurtosis',
 'chroma_stftmax',
 'chroma_stftmean',
 'chroma_stftmedian',
 'chroma_stftmin',
 'chroma_stftskew',
 'chroma_stftstd',
 'mfcckurtosis',
 'mfccmax',
 'mfccmean',
 'mfccmedian',
 'mfccmin',
 'mfccskew',
 'mfccstd',
 'spectral_contrastkurtosis',
 'spectral_contrastmax',
 'spectral_contrastmean',
 'spectral_contrastmedian',
 'spectral_contrastmin',
 'spectral_contrastskew',
 'spectral_contraststd',
 'tonnetzkurtosis',
 'tonnetzmax',
 'tonnetzmean',
 'tonnetzmedian',
 'tonnetzmin',
 'tonnetzskew',
 'tonnetzstd',
 'rmsekurtosis01',
 'rmsemax01',
 'rmsemean01',
 'rmsemedian01',
 'rmsemin01',
 'rmseskew01',
 'rmsestd01',
 'spectral_bandwidthkurtosis01',
 'spectral_bandwidthmax01',
 'spectral_bandwidthmean01',
 'spectral_bandwidthmedian01',
 'spectral_bandwidthmin01',
 'spectral_bandwidthskew01',
 'spectral_bandwidthstd01',
 'spectral_centroidkurtosis01',
 'spectral_centroidmax01',
 'spectral_centroidmean01',
 'spectral_centroidmedian01',
 'spectral_centroidmin01',
 'spectral_centroidskew01',
 'spectral_centroidstd01',
 'spectral_rolloffkurtosis01',
 'spectral_rolloffmax01',
 'spectral_rolloffmean01',
 'spectral_rolloffmedian01',
 'spectral_rolloffmin01',
 'spectral_rolloffskew01',
 'spectral_rolloffstd01',
 'zcrkurtosis01',
 'zcrmax01',
 'zcrmean01',
 'zcrmedian01',
 'zcrmin01',
 'zcrskew01',
 'zcrstd01',
]


bitmap = [
    'Blues',
 'Classical',
 'Country',
 'Easy Listening',
 'Electronic',
 'Experimental',
 'Folk',
 'Hip-Hop',
 'Instrumental',
 'International',
 'Jazz',
 'Old-Time / Historic',
 'Pop',
 'Rock',
 'Soul-RnB',
 'Spoken',
]

nulli = [
     'ALBUM_date_released_year',
    'ALBUM_favorites',
     'ALBUM_listens',
 'ALBUM_tracks',
 'ALBUM_type',
 'ARTIST_favorites',
 'ARTIST_location',
 'TRACK_favorites',
  'ARTIST_location_',
    'TRACK_genres_soloTop'
]

nonNumerici = [
    'ALBUM_tags',
    'ALBUM_title',
    'ARTIST_location_',
    'ARTIST_name',
    'ARTIST_tags',
    'SET_subset',
    'TRACK_genre_top',
    'TRACK_genres',
    'TRACK_genres_all',
    'TRACK_genres_soloTop',
    'TRACK_tags',
    'TRACK_title',
    'TRACK_genres_soloTop'
]

def Diff(li1, li2):
    return list(set(li1)-set(li2))

tutti = list(df.columns)

compl = Diff(tutti, features + bitmap + nonNumerici + nulli+ ['target'])

compl.sort()

compl

['ALBUM_date_released_year_=1905.0',
 'ALBUM_date_released_year_=1907.0',
 'ALBUM_date_released_year_=1909.0',
 'ALBUM_date_released_year_=1911.0',
 'ALBUM_date_released_year_=1912.0',
 'ALBUM_date_released_year_=1913.0',
 'ALBUM_date_released_year_=1916.0',
 'ALBUM_date_released_year_=1930.0',
 'ALBUM_date_released_year_=1965.0',
 'ALBUM_date_released_year_=1967.0',
 'ALBUM_date_released_year_=1968.0',
 'ALBUM_date_released_year_=1969.0',
 'ALBUM_date_released_year_=1971.0',
 'ALBUM_date_released_year_=1973.0',
 'ALBUM_date_released_year_=1974.0',
 'ALBUM_date_released_year_=1976.0',
 'ALBUM_date_released_year_=1978.0',
 'ALBUM_date_released_year_=1979.0',
 'ALBUM_date_released_year_=1980.0',
 'ALBUM_date_released_year_=1981.0',
 'ALBUM_date_released_year_=1982.0',
 'ALBUM_date_released_year_=1984.0',
 'ALBUM_date_released_year_=1985.0',
 'ALBUM_date_released_year_=1986.0',
 'ALBUM_date_released_year_=1987.0',
 'ALBUM_date_released_year_=1988.0',
 'ALBUM_date_released_year_=1989.0',
 

In [17]:
class_name = 'TRACK_genre_top_num'

attributes = Diff(compl, [class_name]) #Diff(compl + features, ('ALBUM_favorites_', 'ALBUM_listens_', 'TRACK_number', 'TRACK_interest'))
X = df[attributes].values
y = df[class_name]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=100, stratify=y)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.1)

#--------------Oversampling:
from imblearn.over_sampling import RandomOverSampler
from imblearn.over_sampling import SMOTE

#ros = RandomOverSampler(random_state=42)
#X_res, y_res = ros.fit_resample(X_train, y_train)


#sm = SMOTE(random_state=42)
#X_res, y_res = sm.fit_resample(X_train, y_train)

X_res = X_train
y_res = y_train

#-------------Undersampling
from imblearn.under_sampling import RandomUnderSampler
from sklearn.preprocessing import RobustScaler

#rus = RandomUnderSampler(random_state=42)
#X_val, y_val = rus.fit_resample(X_val, y_val)



scaler = StandardScaler()
#scaler = MinMaxScaler()
#scaler = RobustScaler()

#scaler.fit(X_res)
#X_res = scaler.transform(X_res)
#X_val = scaler.transform(X_val)
#X_test = scaler.transform(X_test)



unique, counts = np.unique(y_train, return_counts=True)
print("train", dict(zip(unique, counts)))

unique, counts = np.unique(y_res, return_counts=True)
print("bilanciato", dict(zip(unique, counts)))

unique, counts = np.unique(y_val, return_counts=True)
print("validation", dict(zip(unique, counts)))

unique, counts = np.unique(y_test, return_counts=True)
print("test", dict(zip(unique, counts)))


#Trasformo la target value in vettore con 1 sulla posizione del genere giusto
y_res = tf.keras.utils.to_categorical(y_res, 10)
y_val = tf.keras.utils.to_categorical(y_val, 10)
y_test = tf.keras.utils.to_categorical(y_test, 10)

train {0: 1649, 1: 979, 2: 1912, 3: 11405, 4: 7513, 5: 8571, 6: 2240, 7: 2884, 8: 1649, 9: 1110}
bilanciato {0: 1649, 1: 979, 2: 1912, 3: 11405, 4: 7513, 5: 8571, 6: 2240, 7: 2884, 8: 1649, 9: 1110}
validation {0: 183, 1: 112, 2: 180, 3: 1334, 4: 820, 5: 919, 6: 256, 7: 298, 8: 214, 9: 119}
test {0: 204, 1: 121, 2: 233, 3: 1416, 4: 926, 5: 1054, 6: 277, 7: 354, 8: 207, 9: 136}


In [19]:
model = keras.models.load_model('modello_top')

In [22]:
def bb_predict(X):
    return model.predict(X)

def bb_predict_proba(X):
    return model.predict_proba(X)

In [31]:
i2e = 100
x = X_test[i2e]

x

array([ 2.56401300e-01,  3.26644182e-01,  1.60000000e+01,  0.00000000e+00,
        0.00000000e+00,  1.12849879e+00,  3.78584236e-01,  9.99698925e+00,
       -5.57686865e-01,  1.32684696e+00,  5.03120461e+01,  6.58592880e-02,
        3.22131008e-01,  7.41405582e+00, -3.52005768e+01,  3.54666620e-01,
        0.00000000e+00,  1.28893201e+03,  6.71979761e+00, -2.93635702e+00,
        0.00000000e+00,  3.72145146e-01,  4.89173532e-01, -2.38629894e+01,
        7.29694888e-02,  1.26101267e+00,  0.00000000e+00,  1.08154726e+01,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  2.60187168e+01,
        0.00000000e+00,  0.00000000e+00,  1.67980552e+00,  1.35310471e+00,
        1.00000000e+00,  0.00000000e+00, -8.74170840e-01,  0.00000000e+00,
        8.40005875e+00,  0.00000000e+00, -1.07800090e+00, -2.35726857e+00,
       -9.51848149e-01, -2.70090466e+01,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  1.00000000e+00,  4.32885193e+02,
        0.00000000e+00,  

In [32]:
import shap

shap.initjs()

In [33]:
f = lambda x: bb_predict_proba(x)[:, 1]
med = np.median(X_test, axis=0).reshape((1, X_test.shape[1]))

shap_explainer = shap.KernelExplainer(f, med)

`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.


In [34]:
shap_values_single = shap_explainer.shap_values(x, nsamples=1000)

In [35]:
shap.force_plot(shap_explainer.expected_value, shap_values_single, features=x, feature_names=attributes)

In [37]:
shap_values = shap_explainer.shap_values(X_test[0:100,:], nsamples=1000)

`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `

`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `model.predict()` instead.
`model.predict_proba()` is deprecated and will be removed after 2021-01-01. Please use `

In [40]:
shap.force_plot(shap_explainer.expected_value, shap_values, X_test[0:100,:], feature_names=attributes)